Author: Diane Menuz  
Date: June 10, 2025  
Purpose: Compare net radiatometer data between Apogee and NR01 instruments.

# Parameters and Libraries

In [1]:
stationid = 'US-CdM'
start_date = '2023-06-01 0:00' # first data is from June 2023, but no met until October
end_date = '2025-12-31 23:00' # last date of data analysis

micromet_path= "C:/Users/dmenuz/Documents/scripts/MicroMet/src/micromet"
loggerloader_path= "C:/Users/dmenuz/Documents/scripts/loggerloader"
eddy_plots = 'C:/Users/dmenuz/Documents/scripts/eddy'


In [2]:
import pandas as pd
import numpy as np
import importlib.util
import plotly.graph_objects as go
import plotly.express as px

import matplotlib.pyplot as plt
from sklearn.linear_model import LinearRegression
from scipy.stats import linregress
import statsmodels.api as sm
from sklearn.metrics import mean_squared_error
from scipy.signal import correlate
import statsmodels.api as sm
from statsmodels.formula.api import ols


from sqlalchemy import create_engine, inspect
from urllib.parse import quote  
import requests
import json

import plotly.io as pio
pio.renderers.default = 'notebook' 


In [3]:
# import functions
import sys
sys.path.append(micromet_path)
import graphs as mm_graphs

sys.path.append(loggerloader_path)
import loggerloader as ll

sys.path.append(eddy_plots)
import eddy_plots as ed_plot

# Import Data

In [ ]:
spec = importlib.util.spec_from_file_location("dbconnect", "C:/Users/dmenuz/Documents/scripts/supporting_files/dbconnect_cloud.py")
dbconnect = importlib.util.module_from_spec(spec)
spec.loader.exec_module(dbconnect)

engine = dbconnect.postconn_ugs_read()

In [5]:
query = "SELECT * FROM groundwater.amfluxeddy WHERE stationid = %(sid)s AND datetime_start >= %(sdate)s and datetime_start <=%(edate)s"
params = {'sid': stationid, 'sdate': start_date, 'edate': end_date}
try:
    eddy = pd.read_sql(query, engine, params=params)
except Exception as e:
    print(f"Error with parameterized query (named): {e}")
eddy.set_index('datetime_start', inplace=True)

In [6]:
query = "SELECT * FROM groundwater.amfluxmet WHERE stationid = %(sid)s AND datetime_start >= %(sdate)s and datetime_start <=%(edate)s"
params = {'sid': stationid, 'sdate': start_date, 'edate': end_date}
try:
    met = pd.read_sql(query, engine, params=params)
except Exception as e:
    print(f"Error with parameterized query (named): {e}")
met.set_index('datetime_start', inplace=True)

# Fix Lag and Merge Data

In [7]:
# fix -9999 values and identify lag in met data
# note- g_3_1_1 data all 0s for met station for cedar mesa
met['metrad'] = met['netrad_1_1_2']
met['met_ws'] = met['ws']
met.replace(-9999, np.nan, inplace=True)
met_dropna = met.dropna(subset=['metrad'])
eddy.replace(-9999, np.nan, inplace=True)
eddy_dropna = eddy.dropna(subset=['netrad'])
# view lag
ll.plotlystuff([met_dropna,eddy_dropna], ['metrad', 'netrad'])

In [8]:
# fix lag and view merged data
met_fix = met_dropna.copy()
met_fix = met_fix.reset_index()
cutoff_date = pd.to_datetime('2024-03-25 17:30')
met_fix.loc[met_fix['datetime_start'] < cutoff_date, 'datetime_start'] -= pd.to_timedelta('1 hour') 
met_fix.set_index('datetime_start', inplace=True)

merge_fix = pd.merge(eddy[['netrad', 'le', 'h', 'g', 'ws']], met_fix[['metrad','met_ws']], left_index=True, right_index=True, how='inner')
ll.plotlystuff([merge_fix,merge_fix], ['metrad', 'netrad'])

# Review of Monthly Data

In [9]:
# monthly plots, all hourly data
for year in merge_fix.index.year.unique():
    sub1 = merge_fix[(merge_fix.index.year == year)]
    for month in sub1.index.month.unique():
        subset = sub1[(sub1.index.month == month)]
        fig = px.scatter(subset,
            x='netrad',
            y='metrad',
            height=380,
            width=700,
            labels = {'metrad':'Net Radiation from Apogee (W/m2)',
                      'netrad':'Net Radiation from NR01 (W/m2)'},
            title=f'All Hourly Data, Net Radiometer Comparison for {year}-{month}'
        )
        fig.show()

In [10]:
# subset hours on "good" (48 records) days
# and subset days where le, h, or g is null
drop_threshold = 48
merge_fix.dropna(inplace=True, subset=['netrad', 'le', 'h', 'g', 'metrad'])
daily_net = merge_fix.resample('D').count()
daily_net_enough_records = daily_net[daily_net.netrad>=drop_threshold]

hourly_gooddays = merge_fix[merge_fix.index.floor('D').isin(daily_net_enough_records.index)]
print(f'{round((1 - len(hourly_gooddays)/len(merge_fix))*100, 1)}% of records dropped due to lack of {drop_threshold} records/day')

39.2% of records dropped due to lack of 48 records/day


In [11]:
# monthly plots, best hourly data
for year in hourly_gooddays.index.year.unique():
    sub1 = hourly_gooddays[(hourly_gooddays.index.year == year)]
    for month in sub1.index.month.unique():
        subset = sub1[(sub1.index.month == month)]
        fig = px.scatter(subset,
            x='netrad',
            y='metrad',
            height=380,
            width=700,
            labels = {'metrad':'Net Radiation from Apogee (W/m2)',
                      'netrad':'Net Radiation from NR01 (W/m2)'},
            title=f'Subsetted Hourly Data, Net Radiometer Comparison for {year}-{month}'
        )
        fig.show()

# Compare Hourly Data

In [12]:
# ols plot
%matplotlib inline

plt.figure()  
ed_plot.ols_plot(hourly_gooddays['netrad'], hourly_gooddays['metrad'], 
    xlabel=f'Net Radiation from NR01 (W/m2)', 
    ylabel=f'Net Radiation from Apogee (W/m2)', 
    title= f'Hourly Net Radiation Comparison for {stationid}')
plt.tight_layout()  
plt.savefig(f'ols_{stationid}_netrad_subsetted.png')
plt.show()
plt.close() 

<Figure size 1500x1000 with 0 Axes>

In [13]:
ed_plot.student_resid_plot(hourly_gooddays, 'netrad', 'metrad', f'Studentized Residuals for Regression of Net Radiation from Apogee and NR01')

In [14]:
# Bland-Altman
plt.figure()  
f, ax = plt.subplots(1, figsize = (6,4))
sm.graphics.mean_diff_plot(hourly_gooddays['metrad'], hourly_gooddays['netrad'], ax = ax)
plt.tight_layout()  
plt.savefig(f'ba_{stationid}_hourly.png')
plt.show()
plt.close() 

<Figure size 1500x1000 with 0 Axes>

# Daily

In [15]:
# subset out daily data with 48 records
daily_good = hourly_gooddays.resample('D').sum()
daily_good = daily_good[~((daily_good.netrad==0) & (daily_good.metrad==0))]
print(hourly_gooddays.index.month.unique())
print(daily_good.index.month.unique())

Index([10, 11, 12, 1, 2, 3, 4], dtype='int32', name='datetime_start')
Index([10, 11, 12, 1, 2, 3, 4], dtype='int32', name='datetime_start')


In [16]:
# ols plot
%matplotlib inline

plt.figure()  
ed_plot.ols_plot(daily_good['netrad'], daily_good['metrad'], 
    xlabel=f'Net Radiation from NR01 (W/m2)', 
    ylabel=f'Net Radiation from Apogee (W/m2)', 
    title= f'Daily Net Radiation Comparison for {stationid}')
plt.tight_layout()  
plt.savefig(f'daily_ols_{stationid}_netrad_subsetted.png')
plt.show()
plt.close() 

<Figure size 1500x1000 with 0 Axes>

In [17]:
#studentized residuals
ed_plot.student_resid_plot(daily_good, 'netrad', 'metrad', f'Daily Data, Studentized Residuals for Regression of Net Radiation from Apogee and NR01')

In [18]:
## bland-altman
plt.figure()  
f, ax = plt.subplots(1, figsize = (6,4))
sm.graphics.mean_diff_plot(daily_good['metrad'], daily_good['netrad'], ax = ax)
plt.tight_layout()  
plt.savefig(f'daily__subset_ba_{stationid}_netrad.png')
plt.show()
plt.close() 

<Figure size 1500x1000 with 0 Axes>

# Compare met vs. eddy missing data

In [19]:
# # reviewing bad days
# # need to drop -9999 values first
# CB_color_cycle = ['#000000', '#36454F',
#                   '#377eb8', '#ff7f00', '#4daf4a',
#                   '#f781bf', '#a65628', '#984ea3',
#                   '#999999', '#e41a1c', '#dede00']

# daily_good['le_h'] = daily_good['le'] + daily_good['h']

# low_resid_dates = stud_res[stud_res['student_resid']<-1.96].index
# low_resid = daily_good[daily_good.index.isin(low_resid_dates)]
# low_resid['netrad_low_resid_day'] = low_resid['netrad']
# high_resid_dates = stud_res[stud_res['student_resid']>1.96].index
# high_resid = daily_good[daily_good.index.isin(high_resid_dates)]
# high_resid['netrad_high_resid_day'] = high_resid['netrad']

# ll.plotlystuff([high_resid,low_resid,daily_good, daily_good, daily_good, daily_good],
#                ['netrad_high_resid_day','netrad_low_resid_day','netrad','metrad','g', 'le_h'],
#                chrttypes = [ 'markers','markers','lines', 'lines', 'lines', 'lines'],
#                colors = CB_color_cycle[0:7]
#                )

In [20]:
# # which of the bad days have better closure
# high_resid['eddy_closure'] = (high_resid['le']+ high_resid['h'])/(high_resid['netrad']-high_resid['g'])
# high_resid['met_closure'] = (high_resid['le']+ high_resid['h'])/(high_resid['metrad']-high_resid['g'])
# low_resid['eddy_closure'] = (low_resid['le']+ low_resid['h'])/(low_resid['netrad']-low_resid['g'])
# low_resid['met_closure'] = (low_resid['le']+ low_resid['h'])/(low_resid['metrad']-low_resid['g'])
# print("High residual days")
# print(round(high_resid[['eddy_closure', 'met_closure']], 2))
# print("Low residual days")
# print(round(low_resid[['eddy_closure', 'met_closure']], 2))

In [21]:
# # missing data between the two datasets, full datasets
# missing_netrad = len(merge_net[merge_net.netrad.isna()])
# mising_metrad = len(merge_net[merge_net.metrad.isna()])
# missing_le = len(merge_net[merge_net['le'].isna()])
# missing_h = len(merge_net[merge_net['h'].isna()])
# missing_g = len(merge_net[merge_net['g'].isna()])
# missing_dict = {}
# missing_dict['metrad'] = mising_metrad
# missing_dict['netrad'] = missing_netrad
# missing_dict['le'] = missing_le
# missing_dict['h'] = missing_h
# missing_dict['g'] = missing_g

# print('Number of hourly records missing for each parameters in merged dataframe')
# for key, value in missing_dict.items():
#         print(f'{key}: {value}')


In [22]:
# ## clean this up by droppping days with zero records from met data-
# # then determine which sensor has more missing data


# print('Number of records per day for met data')
# print(merge_net['metrad'].resample('D').count().value_counts()[0:6])
# print('Number of records per day for eddy data')
# print(merge_net['netrad'].resample('D').count().value_counts()[0:6]/len(merge_net['netrad'].resample('D').count()))